To run this, press "*Runtime*" and press "*Run all*" on a **free** Tesla T4 Google Colab instance!
<div class="align-center">
  <a href="https://github.com/unslothai/unsloth"><img src="https://github.com/unslothai/unsloth/raw/main/images/unsloth%20new%20logo.png" width="115"></a>
  <a href="https://discord.gg/u54VK8m8tk"><img src="https://github.com/unslothai/unsloth/raw/main/images/Discord button.png" width="145"></a>
  <a href="https://ko-fi.com/unsloth"><img src="https://github.com/unslothai/unsloth/raw/main/images/Kofi button.png" width="145"></a></a> Join Discord if you need help + ⭐ <i>Star us on <a href="https://github.com/unslothai/unsloth">Github</a> </i> ⭐
</div>

To install Unsloth on your own computer, follow the installation instructions on our Github page [here](https://github.com/unslothai/unsloth?tab=readme-ov-file#-installation-instructions).

You will learn how to do [data prep](#Data), how to [train](#Train), how to [run the model](#Inference), & [how to save it](#Save) (eg for Llama.cpp).

**[NEW] Try 2x faster inference in a free Colab for Llama-3.1 8b Instruct [here](https://colab.research.google.com/drive/1T-YBVfnphoVc8E2E854qF3jdia2Ll2W2?usp=sharing)**

Features in the notebook:
1. Uses Maxime Labonne's [FineTome 100K](https://huggingface.co/datasets/mlabonne/FineTome-100k) dataset.
1. Convert ShareGPT to HuggingFace format via `standardize_sharegpt`
2. Train on Completions / Assistant only via `train_on_responses_only`
3. Unsloth now supports Torch 2.4, all TRL & Xformers versions & Python 3.12!

In [1]:
%%capture
!pip install unsloth
# Also get the latest nightly Unsloth!
# !pip uninstall unsloth -y && pip install --upgrade --no-cache-dir --no-deps git+https://github.com/unslothai/unsloth.git

* We support Llama, Mistral, Phi-3, Gemma, Yi, DeepSeek, Qwen, TinyLlama, Vicuna, Open Hermes etc
* We support 16bit LoRA or 4bit QLoRA. Both 2x faster.
* `max_seq_length` can be set to anything, since we do automatic RoPE Scaling via [kaiokendev's](https://kaiokendev.github.io/til) method.
* [**NEW**] We make Gemma-2 9b / 27b **2x faster**! See our [Gemma-2 9b notebook](https://colab.research.google.com/drive/1vIrqH5uYDQwsJ4-OO3DErvuv4pBgVwk4?usp=sharing)
* [**NEW**] To finetune and auto export to Ollama, try our [Ollama notebook](https://colab.research.google.com/drive/1WZDi7APtQ9VsvOrQSSC5DDtxq159j8iZ?usp=sharing)

In [ ]:
TOKEN = "xxx"

In [3]:
MAX_SEQ_LENGTH = 2048

In [4]:
from unsloth import FastLanguageModel
import torch

# 4bit pre quantized models we support for 4x faster downloading + no OOMs.
# More models at https://huggingface.co/unsloth

model, tokenizer = FastLanguageModel.from_pretrained(
    model_name = "unsloth/Llama-3.2-3B-Instruct", # Choose any! We auto support RoPE Scaling internally!
    max_seq_length = MAX_SEQ_LENGTH,
    dtype = None, # None for auto detection. Float16 for Tesla T4, V100, Bfloat16 for Ampere+
    load_in_4bit = True, # Use 4bit quantization to reduce memory usage. Can be False.

    token = TOKEN, # use one if using gated models like meta-llama/Llama-2-7b-hf
)

🦥 Unsloth: Will patch your computer to enable 2x faster free finetuning.
🦥 Unsloth Zoo will now patch everything to make training faster!
==((====))==  Unsloth 2024.12.4: Fast Llama patching. Transformers:4.46.3.
   \\   /|    GPU: Tesla T4. Max memory: 14.748 GB. Platform: Linux.
O^O/ \_/ \    Torch: 2.5.1+cu121. CUDA: 7.5. CUDA Toolkit: 12.1. Triton: 3.1.0
\        /    Bfloat16 = FALSE. FA [Xformers = 0.0.28.post3. FA2 = False]
 "-____-"     Free Apache license: http://github.com/unslothai/unsloth
Unsloth: Fast downloading is enabled - ignore downloading bars which are red colored!


model.safetensors:   0%|          | 0.00/2.24G [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/184 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/54.6k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/9.09M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/454 [00:00<?, ?B/s]

In [5]:
test_prompt = "What is the ELO of this game: 1. e4 e6 2. d4 d5 3. exd5 exd5 4. Bd3 Bd6 5. Ne2 Nf6 6. c4 dxc4 0-1"

In [6]:
from unsloth.chat_templates import get_chat_template
from transformers import TextStreamer

tokenizer = get_chat_template (
    tokenizer,
    chat_template = "llama-3.1",
    mapping={
        "role": "from",
        "content": "value",
        "user": "human",
        "assistant": "gpt",
    },  # ShareGPT style
)
FastLanguageModel.for_inference(model) # Enable native 2x faster inference

streamer = TextStreamer(tokenizer, skip_prompt = True, skip_special_tokens=True)

In [7]:
history = [
    {"role": "user", "content": test_prompt},
]
inputs = tokenizer.apply_chat_template(
    history,
    tokenize = True,
    add_generation_prompt = True, # Must add for generation
    return_tensors = "pt",
)

_ = model.generate(input_ids=inputs, streamer=streamer)

The attention mask is not set and cannot be inferred from input because pad token is same as eos token. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.


To determine the ELO of this game, we need to analyze the moves and the overall strategy.

The game appears to be a Sicilian Defense, one of the most popular and aggressive openings in chess. The moves 1.e4 e6 2.d4 d5 3.exd5 exd5 4.Bd3 Bd6 5.Ne2 Nf6 are typical of the Sicilian Defense, and the moves 6.c4 dxc4 0-1 seem to be a variation of the Alapin Variation.

However, without knowing the exact ELO rating of the players, we can only estimate the ELO rating of the game.

Assuming the players are of similar skill levels, the game's ELO rating can be estimated as follows:

- The Sicilian Defense is considered a very aggressive and complex opening, which can lead to a high number of ELO ratings.
- The Alapin Variation is considered a solid and positional opening, which can lead to a lower ELO rating.
- The game's outcome (0-1) suggests that the player playing white made a mistake or underestimated their opponent.

Considering these factors, I would estimate the ELO rating of the game to b

In [8]:
from threading import Thread
from transformers import TextIteratorStreamer

streamer2 = TextIteratorStreamer(tokenizer)

prompt = tokenizer.apply_chat_template (
    history,
    tokenize = False,
    add_generation_prompt = True, # Must add for generation
)

inputs = tokenizer([prompt], return_tensors="pt")

# Run the generation in a separate thread, so that we can fetch the generated text in a non-blocking way.
generation_kwargs = dict(inputs, streamer=streamer2)

thread = Thread(target=model.generate, kwargs=generation_kwargs)
thread.start()

generated_text = ""
for new_text in streamer2:
    generated_text += new_text
    print(new_text, end="", flush=True)

<|begin_of_text|><|begin_of_text|><|start_header_id|>system<|end_header_id|>

Cutting Knowledge Date: December 2023
Today Date: 26 July 2024

<|eot_id|><|start_header_id|>user<|end_header_id|>

What is the ELO of this game: 1. e4 e6 2. d4 d5 3. exd5 exd5 4. Bd3 Bd6 5. Ne2 Nf6 6. c4 dxc4 0-1<|eot_id|><|start_header_id|>assistant<|end_header_id|>

To determine the ELO rating of this game, we need to analyze the moves and the outcome.

The ELO rating of a game is determined by the difference in rating between the two players. However, since this is a one-move game, we can't directly calculate the ELO rating. But we can calculate the ELO rating of each player based on their moves.

The moves are:
1. e4 e6
2. d4 d5
3. exd5 exd5
4. Bd3 Bd6
5. Ne2 Nf6
6. c4 dxc4

This is a Sicilian Defense, a popular opening in chess. The game is not a typical one, as it ends in a draw (0-0-1). To calculate the ELO rating, we need to compare the moves of both players.

In this case, White (ELO rating of White

Before Training:

We now add LoRA adapters so we only need to update 1 to 10% of all parameters!

In [9]:
model = FastLanguageModel.get_peft_model(
    model,
    r = 4, # Choose any number > 0 ! Suggested 8, 16, 32, 64, 128
    target_modules = ["q_proj", "k_proj", "v_proj", "o_proj",
                      "gate_proj", "up_proj", "down_proj",],
    lora_alpha = 8,
    lora_dropout = 0.8, # Supports any, but = 0 is optimized
    bias = "none",    # Supports any, but = "none" is optimized
    # [NEW] "unsloth" uses 30% less VRAM, fits 2x larger batch sizes!
    use_gradient_checkpointing = "unsloth", # True or "unsloth" for very long context
    random_state = 3407,
    use_rslora = False,  # We support rank stabilized LoRA
    loftq_config = None, # And LoftQ
)

Unsloth: Dropout = 0 is supported for fast patching. You are using dropout = 0.8.
Unsloth will patch all other layers, except LoRA matrices, causing a performance hit.
Unsloth 2024.12.4 patched 28 layers with 0 QKV layers, 0 O layers and 0 MLP layers.


<a name="Data"></a>
### Data Prep
We now use the `Llama-3.1` format for conversation style finetunes. We use [Maxime Labonne's FineTome-100k](https://huggingface.co/datasets/mlabonne/FineTome-100k) dataset in ShareGPT style. But we convert it to HuggingFace's normal multiturn format `("role", "content")` instead of `("from", "value")`/ Llama-3 renders multi turn conversations like below:

```
<|begin_of_text|><|start_header_id|>user<|end_header_id|>

Hello!<|eot_id|><|start_header_id|>assistant<|end_header_id|>

Hey there! How are you?<|eot_id|><|start_header_id|>user<|end_header_id|>

I'm great thanks!<|eot_id|>
```

We use our `get_chat_template` function to get the correct chat template. We support `zephyr, chatml, mistral, llama, alpaca, vicuna, vicuna_old, phi3, llama3` and more.

In [10]:
from unsloth.chat_templates import get_chat_template

tokenizer = get_chat_template(
    tokenizer,
    chat_template = "llama-3.1",
)

def formatting_prompts_func(examples):
    convos = examples["conversations"]
    texts = [tokenizer.apply_chat_template(convo, tokenize = False, add_generation_prompt = False) for convo in convos]
    return { "text" : texts, }
pass

from datasets import load_dataset, Dataset
# dataset = load_dataset("mlabonne/FineTome-100k", split = "train")
dataset = load_dataset("pjarbas312/chessllm", split="train")

README.md:   0%|          | 0.00/87.0 [00:00<?, ?B/s]

(…)ichess_curriculum_127k_2300-3000.parquet:   0%|          | 0.00/73.7M [00:00<?, ?B/s]

Generating train split:   0%|          | 0/128927 [00:00<?, ? examples/s]

In [11]:
dataset[5]

{'average_elo': 2300.0,
 'transcript': '1. d4 d5 2. c4 e6 3. cxd5 exd5 4. Nc3 c6 5. Nf3 f5 6. Bg5 Nf6 7. e3 Bd6 8. Bd3 O-O 9. O-O Qe8 10. Bxf6 Rxf6 11. a3 Be6 12. Ne5 Bxe5 13. dxe5 Rh6 14. f4 Nd7 15. Ne2 Nc5 16. Nd4 Ne4 17. Bxe4 fxe4 18. b4 b6 19. Rc1 Rc8 20. Qe2 c5 21. Nb5 Qg6 22. Nd6 Rc7 23. f5 Bxf5 24. Nxf5 Rh5 25. g4 Rg5 26. h3 h5 27. Rf4 Rf7 28. Kf2 Rfxf5 29. Rxf5 Rxf5+ 30. gxf5 Qxf5+ 31. Ke1 Qxe5 32. bxc5 bxc5 33. Rxc5 Qg3+ 34. Kd2 Qe5 35. Qb5 Qh2+ 36. Kc3 Qf2 37. Qe8+ Kh7 38. Qxh5+ Kg8 39. Rc8+ Qf8 40. Rxf8+ Kxf8 41. Qf5+ Ke7 42. Qxd5 Kf6 43. Qxe4 Kg5 44. Qd4 Kh6 45. Qxa7 g5 46. Qa6+ Kh5 47. Qa5 Kh4 48. Qxg5+ 1-0'}

In [12]:
def convert_dataset(data_list):
  converted_dataset = []
  for data in data_list:
    conversations = []
    conversations.append({"from": "human", "value": f"Guess the elo of this game: {data['transcript']}"})
    conversations.append({"from": "gpt", "value": f"The average elo of the game is: {data['average_elo']}"})
    converted_dataset.append({"conversations": conversations})
  return converted_dataset

In [13]:
dataset = convert_dataset(dataset)

We now use `standardize_sharegpt` to convert ShareGPT style datasets into HuggingFace's generic format. This changes the dataset from looking like:
```
{"from": "system", "value": "You are an assistant"}
{"from": "human", "value": "What is 2+2?"}
{"from": "gpt", "value": "It's 4."}
```
to
```
{"role": "system", "content": "You are an assistant"}
{"role": "user", "content": "What is 2+2?"}
{"role": "assistant", "content": "It's 4."}
```

In [14]:
from unsloth.chat_templates import standardize_sharegpt
dataset = standardize_sharegpt(Dataset.from_list(dataset))
dataset = dataset.map(formatting_prompts_func, batched = True,)

Standardizing format:   0%|          | 0/128927 [00:00<?, ? examples/s]

Map:   0%|          | 0/128927 [00:00<?, ? examples/s]

We look at how the conversations are structured for item 5:

In [15]:
dataset[5]["conversations"]

[{'content': 'Guess the elo of this game: 1. d4 d5 2. c4 e6 3. cxd5 exd5 4. Nc3 c6 5. Nf3 f5 6. Bg5 Nf6 7. e3 Bd6 8. Bd3 O-O 9. O-O Qe8 10. Bxf6 Rxf6 11. a3 Be6 12. Ne5 Bxe5 13. dxe5 Rh6 14. f4 Nd7 15. Ne2 Nc5 16. Nd4 Ne4 17. Bxe4 fxe4 18. b4 b6 19. Rc1 Rc8 20. Qe2 c5 21. Nb5 Qg6 22. Nd6 Rc7 23. f5 Bxf5 24. Nxf5 Rh5 25. g4 Rg5 26. h3 h5 27. Rf4 Rf7 28. Kf2 Rfxf5 29. Rxf5 Rxf5+ 30. gxf5 Qxf5+ 31. Ke1 Qxe5 32. bxc5 bxc5 33. Rxc5 Qg3+ 34. Kd2 Qe5 35. Qb5 Qh2+ 36. Kc3 Qf2 37. Qe8+ Kh7 38. Qxh5+ Kg8 39. Rc8+ Qf8 40. Rxf8+ Kxf8 41. Qf5+ Ke7 42. Qxd5 Kf6 43. Qxe4 Kg5 44. Qd4 Kh6 45. Qxa7 g5 46. Qa6+ Kh5 47. Qa5 Kh4 48. Qxg5+ 1-0',
  'role': 'user'},
 {'content': 'The average elo of the game is: 2300.0', 'role': 'assistant'}]

And we see how the chat template transformed these conversations.

**[Notice]** Llama 3.1 Instruct's default chat template default adds `"Cutting Knowledge Date: December 2023\nToday Date: 26 July 2024"`, so do not be alarmed!

In [16]:
dataset[5]["text"]

'<|begin_of_text|><|start_header_id|>system<|end_header_id|>\n\nCutting Knowledge Date: December 2023\nToday Date: 26 July 2024\n\n<|eot_id|><|start_header_id|>user<|end_header_id|>\n\nGuess the elo of this game: 1. d4 d5 2. c4 e6 3. cxd5 exd5 4. Nc3 c6 5. Nf3 f5 6. Bg5 Nf6 7. e3 Bd6 8. Bd3 O-O 9. O-O Qe8 10. Bxf6 Rxf6 11. a3 Be6 12. Ne5 Bxe5 13. dxe5 Rh6 14. f4 Nd7 15. Ne2 Nc5 16. Nd4 Ne4 17. Bxe4 fxe4 18. b4 b6 19. Rc1 Rc8 20. Qe2 c5 21. Nb5 Qg6 22. Nd6 Rc7 23. f5 Bxf5 24. Nxf5 Rh5 25. g4 Rg5 26. h3 h5 27. Rf4 Rf7 28. Kf2 Rfxf5 29. Rxf5 Rxf5+ 30. gxf5 Qxf5+ 31. Ke1 Qxe5 32. bxc5 bxc5 33. Rxc5 Qg3+ 34. Kd2 Qe5 35. Qb5 Qh2+ 36. Kc3 Qf2 37. Qe8+ Kh7 38. Qxh5+ Kg8 39. Rc8+ Qf8 40. Rxf8+ Kxf8 41. Qf5+ Ke7 42. Qxd5 Kf6 43. Qxe4 Kg5 44. Qd4 Kh6 45. Qxa7 g5 46. Qa6+ Kh5 47. Qa5 Kh4 48. Qxg5+ 1-0<|eot_id|><|start_header_id|>assistant<|end_header_id|>\n\nThe average elo of the game is: 2300.0<|eot_id|>'

<a name="Train"></a>
### Train the model
Now let's use Huggingface TRL's `SFTTrainer`! More docs here: [TRL SFT docs](https://huggingface.co/docs/trl/sft_trainer). We do 60 steps to speed things up, but you can set `num_train_epochs=1` for a full run, and turn off `max_steps=None`. We also support TRL's `DPOTrainer`!

In [ ]:
from trl import SFTTrainer
from transformers import TrainingArguments, DataCollatorForSeq2Seq
from unsloth import is_bfloat16_supported

from google.colab import drive
drive.mount('/content/drive')

trainer = SFTTrainer(
    model = model,
    tokenizer = tokenizer,
    train_dataset = dataset,
    dataset_text_field = "text",
    max_seq_length = MAX_SEQ_LENGTH,
    data_collator = DataCollatorForSeq2Seq(tokenizer = tokenizer),
    dataset_num_proc = 2,
    packing = False, # Can make training 5x faster for short sequences.
    args = TrainingArguments(
        per_device_train_batch_size = 2,
        gradient_accumulation_steps = 4,
        warmup_steps = 5,
        num_train_epochs = 1, # Set this for 1 full training run.
        max_steps = 2500,
        learning_rate = 2e-4,
        fp16 = not is_bfloat16_supported(),
        bf16 = is_bfloat16_supported(),
        logging_steps = 1,
        optim = "adamw_8bit",
        weight_decay = 0.01,
        lr_scheduler_type = "linear",
        seed = 3407,
        output_dir = "xxx",
        report_to = "none", # Use this for WandB etc,
        # For period checkpointing - https://docs.unsloth.ai/basics/finetuning-from-last-checkpoint
        save_strategy = "steps",
        save_steps = 100,
    ),
)

Mounted at /content/drive


Map (num_proc=2):   0%|          | 0/128927 [00:00<?, ? examples/s]

max_steps is given, it will override any value given in num_train_epochs


We also use Unsloth's `train_on_completions` method to only train on the assistant outputs and ignore the loss on the user's inputs.

In [18]:
from unsloth.chat_templates import train_on_responses_only
trainer = train_on_responses_only(
    trainer,
    instruction_part = "<|start_header_id|>user<|end_header_id|>\n\n",
    response_part = "<|start_header_id|>assistant<|end_header_id|>\n\n",
)

Map:   0%|          | 0/128927 [00:00<?, ? examples/s]

We verify masking is actually done:

In [19]:
tokenizer.decode(trainer.train_dataset[5]["input_ids"])

'<|begin_of_text|><|start_header_id|>system<|end_header_id|>\n\nCutting Knowledge Date: December 2023\nToday Date: 26 July 2024\n\n<|eot_id|><|start_header_id|>user<|end_header_id|>\n\nGuess the elo of this game: 1. d4 d5 2. c4 e6 3. cxd5 exd5 4. Nc3 c6 5. Nf3 f5 6. Bg5 Nf6 7. e3 Bd6 8. Bd3 O-O 9. O-O Qe8 10. Bxf6 Rxf6 11. a3 Be6 12. Ne5 Bxe5 13. dxe5 Rh6 14. f4 Nd7 15. Ne2 Nc5 16. Nd4 Ne4 17. Bxe4 fxe4 18. b4 b6 19. Rc1 Rc8 20. Qe2 c5 21. Nb5 Qg6 22. Nd6 Rc7 23. f5 Bxf5 24. Nxf5 Rh5 25. g4 Rg5 26. h3 h5 27. Rf4 Rf7 28. Kf2 Rfxf5 29. Rxf5 Rxf5+ 30. gxf5 Qxf5+ 31. Ke1 Qxe5 32. bxc5 bxc5 33. Rxc5 Qg3+ 34. Kd2 Qe5 35. Qb5 Qh2+ 36. Kc3 Qf2 37. Qe8+ Kh7 38. Qxh5+ Kg8 39. Rc8+ Qf8 40. Rxf8+ Kxf8 41. Qf5+ Ke7 42. Qxd5 Kf6 43. Qxe4 Kg5 44. Qd4 Kh6 45. Qxa7 g5 46. Qa6+ Kh5 47. Qa5 Kh4 48. Qxg5+ 1-0<|eot_id|><|start_header_id|>assistant<|end_header_id|>\n\nThe average elo of the game is: 2300.0<|eot_id|>'

In [20]:
space = tokenizer(" ", add_special_tokens = False).input_ids[0]
tokenizer.decode([space if x == -100 else x for x in trainer.train_dataset[5]["labels"]])

'                                                                                                                                                                                                                                                                                                                                                                                                                                                             \n\nThe average elo of the game is: 2300.0<|eot_id|>'

We can see the System and Instruction prompts are successfully masked!

In [21]:
#@title Show current memory stats
gpu_stats = torch.cuda.get_device_properties(0)
start_gpu_memory = round(torch.cuda.max_memory_reserved() / 1024 / 1024 / 1024, 3)
max_memory = round(gpu_stats.total_memory / 1024 / 1024 / 1024, 3)
print(f"GPU = {gpu_stats.name}. Max memory = {max_memory} GB.")
print(f"{start_gpu_memory} GB of memory reserved.")

GPU = Tesla T4. Max memory = 14.748 GB.
2.836 GB of memory reserved.


In [22]:
trainer_stats = trainer.train(
    # Uncomment if running from a checkpoint
    resume_from_checkpoint = True
)

/usr/local/lib/python3.10/dist-packages/transformers/trainer.py:3354: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  torch.load(os.path.join(checkpoint, OPTIMIZER_NAME), map_

In [23]:
#@title Show final memory and time stats
used_memory = round(torch.cuda.max_memory_reserved() / 1024 / 1024 / 1024, 3)
used_memory_for_lora = round(used_memory - start_gpu_memory, 3)
used_percentage = round(used_memory         /max_memory*100, 3)
lora_percentage = round(used_memory_for_lora/max_memory*100, 3)
print(f"{trainer_stats.metrics['train_runtime']} seconds used for training.")
print(f"{round(trainer_stats.metrics['train_runtime']/60, 2)} minutes used for training.")
print(f"Peak reserved memory = {used_memory} GB.")
print(f"Peak reserved memory for training = {used_memory_for_lora} GB.")
print(f"Peak reserved memory % of max memory = {used_percentage} %.")
print(f"Peak reserved memory for training % of max memory = {lora_percentage} %.")

27.8136 seconds used for training.
0.46 minutes used for training.
Peak reserved memory = 4.119 GB.
Peak reserved memory for training = 1.283 GB.
Peak reserved memory % of max memory = 27.929 %.
Peak reserved memory for training % of max memory = 8.699 %.


<a name="Save"></a>
### Saving, loading finetuned models
To save the final model as LoRA adapters, either use Huggingface's `push_to_hub` for an online save or `save_pretrained` for a local save.

**[NOTE]** This ONLY saves the LoRA adapters, and not the full model. To save to 16bit or GGUF, scroll down!

In [24]:
model.save_pretrained("lora_model") # Local saving
tokenizer.save_pretrained("lora_model")

# model_path = "samlama111/lora_model"
model_path = "EPark25/llama_chess"

model.push_to_hub(model_path, token = TOKEN) # Online saving
tokenizer.push_to_hub(model_path, token = TOKEN) # Online saving

README.md:   0%|          | 0.00/5.18k [00:00<?, ?B/s]

  0%|          | 0/1 [00:00<?, ?it/s]

adapter_model.safetensors:   0%|          | 0.00/24.4M [00:00<?, ?B/s]

Saved model to https://huggingface.co/EPark25/llama_chess


No files have been modified since last commit. Skipping to prevent empty commit.


 You can also use a `TextStreamer` for continuous inference - so you can see the generation token by token, instead of waiting the whole time!

<a name="Inference"></a>
### Inference
Let's run the model! You can change the instruction and input - leave the output blank!

**[NEW] Try 2x faster inference in a free Colab for Llama-3.1 8b Instruct [here](https://colab.research.google.com/drive/1T-YBVfnphoVc8E2E854qF3jdia2Ll2W2?usp=sharing)**

We use `min_p = 0.1` and `temperature = 1.5`. Read this [Tweet](https://x.com/menhguin/status/1826132708508213629) for more information on why.

In [25]:
model, tokenizer = FastLanguageModel.from_pretrained(
    model_name = "EPark25/llama_chess", # Choose any! We auto support RoPE Scaling internally!
    max_seq_length = MAX_SEQ_LENGTH,
    dtype = None, # None for auto detection. Float16 for Tesla T4, V100, Bfloat16 for Ampere+
    load_in_4bit = True, # Use 4bit quantization to reduce memory usage. Can be False.

    token = TOKEN, # use one if using gated models like meta-llama/Llama-2-7b-hf
)

==((====))==  Unsloth 2024.12.4: Fast Llama patching. Transformers:4.46.3.
   \\   /|    GPU: Tesla T4. Max memory: 14.748 GB. Platform: Linux.
O^O/ \_/ \    Torch: 2.5.1+cu121. CUDA: 7.5. CUDA Toolkit: 12.1. Triton: 3.1.0
\        /    Bfloat16 = FALSE. FA [Xformers = 0.0.28.post3. FA2 = False]
 "-____-"     Free Apache license: http://github.com/unslothai/unsloth
Unsloth: Fast downloading is enabled - ignore downloading bars which are red colored!


adapter_model.safetensors:   0%|          | 0.00/24.4M [00:00<?, ?B/s]

In [26]:
tokenizer = get_chat_template (
    tokenizer,
    chat_template = "llama-3.1",
    mapping={
        "role": "from",
        "content": "value",
        "user": "human",
        "assistant": "gpt",
    },  # ShareGPT style
)
FastLanguageModel.for_inference(model) # Enable native 2x faster inference

streamer = TextIteratorStreamer(tokenizer, skip_prompt=True, skip_special_tokens=True)

In [27]:
history = [
    {"role": "user", "content": test_prompt},
]

prompt = tokenizer.apply_chat_template (
    history,
    tokenize = False,
    add_generation_prompt = True, # Must add for generation
)

inputs = tokenizer([prompt], return_tensors="pt")

# Run the generation in a separate thread, so that we can fetch the generated text in a non-blocking way.
generation_kwargs = dict(inputs, streamer=streamer)

thread = Thread(target=model.generate, kwargs=generation_kwargs)
thread.start()

generated_text = ""
for new_text in streamer:
    generated_text += new_text
    print(new_text, end="", flush=True)

The average ELO of the game is: 2336.5

In [28]:
history = [
    {"role": "user", "content": "who is the first president of the USA"},
]

prompt = tokenizer.apply_chat_template (
    history,
    tokenize = False,
    add_generation_prompt = True, # Must add for generation
)

inputs = tokenizer([prompt], return_tensors="pt")

# Run the generation in a separate thread, so that we can fetch the generated text in a non-blocking way.
generation_kwargs = dict(inputs, streamer=streamer)

thread = Thread(target=model.generate, kwargs=generation_kwargs)
thread.start()

generated_text = ""
for new_text in streamer:
    generated_text += new_text
    print(new_text, end="", flush=True)

The first president of the United States of America is George Washington. He was inaugurated as the first president on April 30, 1789, and served two terms in office until March 4, 1797.

### Saving to float16 for VLLM

We also support saving to `float16` directly. Select `merged_16bit` for float16 or `merged_4bit` for int4. We also allow `lora` adapters as a fallback. Use `push_to_hub_merged` to upload to your Hugging Face account! You can go to https://huggingface.co/settings/tokens for your personal tokens.

In [29]:
# Merge to 16bit
if False: model.save_pretrained_merged("model", tokenizer, save_method = "merged_16bit",)
if False: model.push_to_hub_merged("hf/model", tokenizer, save_method = "merged_16bit", token = "")

# Merge to 4bit
if False: model.save_pretrained_merged("model", tokenizer, save_method = "merged_4bit",)
if False: model.push_to_hub_merged("hf/model", tokenizer, save_method = "merged_4bit", token = "")

# Just LoRA adapters
if False: model.save_pretrained_merged("model", tokenizer, save_method = "lora",)
if False: model.push_to_hub_merged("hf/model", tokenizer, save_method = "lora", token = "")

### GGUF / llama.cpp Conversion
To save to `GGUF` / `llama.cpp`, we support it natively now! We clone `llama.cpp` and we default save it to `q8_0`. We allow all methods like `q4_k_m`. Use `save_pretrained_gguf` for local saving and `push_to_hub_gguf` for uploading to HF.

Some supported quant methods (full list on our [Wiki page](https://github.com/unslothai/unsloth/wiki#gguf-quantization-options)):
* `q8_0` - Fast conversion. High resource use, but generally acceptable.
* `q4_k_m` - Recommended. Uses Q6_K for half of the attention.wv and feed_forward.w2 tensors, else Q4_K.
* `q5_k_m` - Recommended. Uses Q6_K for half of the attention.wv and feed_forward.w2 tensors, else Q5_K.

[**NEW**] To finetune and auto export to Ollama, try our [Ollama notebook](https://colab.research.google.com/drive/1WZDi7APtQ9VsvOrQSSC5DDtxq159j8iZ?usp=sharing)

In [30]:
# Save to 8bit Q8_0
if False: model.save_pretrained_gguf("model", tokenizer,)
# Remember to go to https://huggingface.co/settings/tokens for a token!
# And change hf to your username!
if False: model.push_to_hub_gguf("hf/model", tokenizer, token = "")

# Save to 16bit GGUF
if False: model.save_pretrained_gguf("model", tokenizer, quantization_method = "f16")
if False: model.push_to_hub_gguf("hf/model", tokenizer, quantization_method = "f16", token = "")

# Save to q4_k_m GGUF
if False: model.save_pretrained_gguf("model", tokenizer, quantization_method = "q4_k_m")
if False: model.push_to_hub_gguf("hf/model", tokenizer, quantization_method = "q4_k_m", token = "")

# Save to multiple GGUF options - much faster if you want multiple!
if False:
    model.push_to_hub_gguf(
        "hf/model", # Change hf to your username!
        tokenizer,
        quantization_method = ["q4_k_m", "q8_0", "q5_k_m",],
        token = "", # Get a token at https://huggingface.co/settings/tokens
    )

Now, use the `model-unsloth.gguf` file or `model-unsloth-Q4_K_M.gguf` file in `llama.cpp` or a UI based system like `GPT4All`. You can install GPT4All by going [here](https://gpt4all.io/index.html).

**[NEW] Try 2x faster inference in a free Colab for Llama-3.1 8b Instruct [here](https://colab.research.google.com/drive/1T-YBVfnphoVc8E2E854qF3jdia2Ll2W2?usp=sharing)**

And we're done! If you have any questions on Unsloth, we have a [Discord](https://discord.gg/u54VK8m8tk) channel! If you find any bugs or want to keep updated with the latest LLM stuff, or need help, join projects etc, feel free to join our Discord!

Some other links:
1. Zephyr DPO 2x faster [free Colab](https://colab.research.google.com/drive/15vttTpzzVXv_tJwEk-hIcQ0S9FcEWvwP?usp=sharing)
2. Llama 7b 2x faster [free Colab](https://colab.research.google.com/drive/1lBzz5KeZJKXjvivbYvmGarix9Ao6Wxe5?usp=sharing)
3. TinyLlama 4x faster full Alpaca 52K in 1 hour [free Colab](https://colab.research.google.com/drive/1AZghoNBQaMDgWJpi4RbffGM1h6raLUj9?usp=sharing)
4. CodeLlama 34b 2x faster [A100 on Colab](https://colab.research.google.com/drive/1y7A0AxE3y8gdj4AVkl2aZX47Xu3P1wJT?usp=sharing)
5. Mistral 7b [free Kaggle version](https://www.kaggle.com/code/danielhanchen/kaggle-mistral-7b-unsloth-notebook)
6. We also did a [blog](https://huggingface.co/blog/unsloth-trl) with 🤗 HuggingFace, and we're in the TRL [docs](https://huggingface.co/docs/trl/main/en/sft_trainer#accelerate-fine-tuning-2x-using-unsloth)!
7. `ChatML` for ShareGPT datasets, [conversational notebook](https://colab.research.google.com/drive/1Aau3lgPzeZKQ-98h69CCu1UJcvIBLmy2?usp=sharing)
8. Text completions like novel writing [notebook](https://colab.research.google.com/drive/1ef-tab5bhkvWmBOObepl1WgJvfvSzn5Q?usp=sharing)
9. [**NEW**] We make Phi-3 Medium / Mini **2x faster**! See our [Phi-3 Medium notebook](https://colab.research.google.com/drive/1hhdhBa1j_hsymiW9m-WzxQtgqTH_NHqi?usp=sharing)
10. [**NEW**] We make Gemma-2 9b / 27b **2x faster**! See our [Gemma-2 9b notebook](https://colab.research.google.com/drive/1vIrqH5uYDQwsJ4-OO3DErvuv4pBgVwk4?usp=sharing)
11. [**NEW**] To finetune and auto export to Ollama, try our [Ollama notebook](https://colab.research.google.com/drive/1WZDi7APtQ9VsvOrQSSC5DDtxq159j8iZ?usp=sharing)
12. [**NEW**] We make Mistral NeMo 12B 2x faster and fit in under 12GB of VRAM! [Mistral NeMo notebook](https://colab.research.google.com/drive/17d3U-CAIwzmbDRqbZ9NnpHxCkmXB6LZ0?usp=sharing)

<div class="align-center">
  <a href="https://github.com/unslothai/unsloth"><img src="https://github.com/unslothai/unsloth/raw/main/images/unsloth%20new%20logo.png" width="115"></a>
  <a href="https://discord.gg/u54VK8m8tk"><img src="https://github.com/unslothai/unsloth/raw/main/images/Discord.png" width="145"></a>
  <a href="https://ko-fi.com/unsloth"><img src="https://github.com/unslothai/unsloth/raw/main/images/Kofi button.png" width="145"></a></a> Support our work if you can! Thanks!
</div>